# PISA example notebook 
Isopolygons calculated using Mapbox

In [53]:
from functools import partial

from optimization import jg_opt
from pisa.administrative_area import AdministrativeArea
from pisa.facilities import Facilities
from pisa.population import WorldpopPopulation
from pisa.population_served_by_isopolygons import get_population_served_by_isopolygons
from pisa.visualisation import (
    plot_facilities,
    plot_isochrones,
    plot_population,
    plot_population_heatmap,
)


### Define Administrative Area

Remark: the administrative area is a country because of the package that we use for fetching the data (gadm).

The naming is somewhat confusing: we want the administrative area to be a subset of a country (in this case, the administrative area should be Baucau). 

Should be easy to fix if [this change](https://github.com/Analytics-for-a-Better-World/Public-Infrastructure-Service-Access/issues/59) is implemented.

In [54]:
timor_leste = AdministrativeArea(country_name="Timor-Leste", admin_level=1)

# these are the boundaries of Baucau
# type: Polygon
baucau = timor_leste.get_admin_area_boundaries("Baucau")

INFO:pisa.administrative_area:Validating country name: Timor-Leste
INFO:pisa.administrative_area:Country name 'Timor-Leste' validated successfully
INFO:pisa.administrative_area:Retrieving boundaries of all administrative areas of level 1 for country Timor-Leste


### Facilities


Create instance of Facilities class for the selected administrative area with 
OSM tags for desired facilities (hospitals by default). 

In [55]:
hospitals = Facilities(admin_area_boundaries=baucau)

#### Get existing facilities (in this example, hospitals) from OSM

In [56]:
existing_hospitals_df = hospitals.get_existing_facilities()

INFO:pisa.facilities:Retrieving existing facilities with tags {'amenity': 'hospital', 'building': 'hospital'} using OSM.
INFO:pisa.facilities:Successfully retrieved existing facilities from OSM.


In [57]:
plot_facilities(existing_hospitals_df, baucau)

#### Estimate potential locations for new facilities


In [58]:
potential_hospitals_df = hospitals.estimate_potential_facilities(spacing=0.05)

plot_facilities(potential_hospitals_df, baucau)

### Get population 
In this example, from WorldPop

In [59]:
population_gdf = WorldpopPopulation(
    admin_area_boundaries=baucau, iso3_country_code=timor_leste.get_iso3_country_code()
).get_population_gdf()


In [60]:
plot_population_heatmap(population_gdf, baucau)

In [61]:
plot_population(population_gdf, baucau, random_sample_n=1000)

### Calculate isopolygons

Here we make some choices:
- distance type
- distance values
- mode of transport 

Valid values for constants are in the script `pisa.constants`

In [62]:
DISTANCE_TYPE = "length"

DISTANCE_VALUES = [2000, 5000, 10000]

MODE_OF_TRANSPORT = "driving"

#### Using Mapbox API

In [63]:
import os

from dotenv import load_dotenv

# keep the API keys in a `.env` file in the local root directory
load_dotenv()


MAPBOX_API_TOKEN = os.getenv("MAPBOX_API_TOKEN")
CBC_SOLVER_PATH = os.getenv("CBC_SOLVER_PATH")  # path to the cbc executable (e.g. /opt/homebrew/bin/cbc)


#### Calculate isopolygons for existing facilities

In [64]:
from pisa.isopolygons import MapboxIsopolygonCalculator

isopolygons_existing_facilities = MapboxIsopolygonCalculator(
        facilities_df=existing_hospitals_df,
        distance_type=DISTANCE_TYPE,
        distance_values=DISTANCE_VALUES,
        mode_of_transport=MODE_OF_TRANSPORT,
        mapbox_api_token=MAPBOX_API_TOKEN,
    ).calculate_isopolygons()

INFO:pisa.utils:
=== Cache Status ===
INFO:pisa.utils:Function: _fetch_isopolygons
INFO:pisa.utils:Cache file: mapbox_cache/beef6be98b3595b653799ba604e3cbb908612f9813f710a6b7eaf967a72316bd.pkl
INFO:pisa.utils:Cache HIT - Loading cached result
INFO:pisa.utils:
=== Cache Status ===
INFO:pisa.utils:Function: _fetch_isopolygons
INFO:pisa.utils:Cache file: mapbox_cache/705230117b30f891afab547e28aa1bd9b9660bd2f2049a4f991c8d418d338923.pkl
INFO:pisa.utils:Cache HIT - Loading cached result
INFO:pisa.utils:
=== Cache Status ===
INFO:pisa.utils:Function: _fetch_isopolygons
INFO:pisa.utils:Cache file: mapbox_cache/f5a5b342423a738b9a80e6ad477383d48ca089b03ace7bbe53dfc88a67932ae3.pkl
INFO:pisa.utils:Cache HIT - Loading cached result
INFO:pisa.utils:
=== Cache Status ===
INFO:pisa.utils:Function: _fetch_isopolygons
INFO:pisa.utils:Cache file: mapbox_cache/74b773b32199a8e47595996a08f85c74fe06725847dcef1c0cef1946256a1392.pkl
INFO:pisa.utils:Cache HIT - Loading cached result
INFO:pisa.utils:
=== Cache S

In [65]:
plot_isochrones(isopolygons_existing_facilities, baucau)

#### Calculate isopolygons for potential facilities

In [66]:
isopolygons_potential_facilities = MapboxIsopolygonCalculator(
        facilities_df=potential_hospitals_df,
        distance_type=DISTANCE_TYPE,
        distance_values=DISTANCE_VALUES,
        mode_of_transport=MODE_OF_TRANSPORT,
        mapbox_api_token=MAPBOX_API_TOKEN,
    ).calculate_isopolygons()

INFO:pisa.utils:
=== Cache Status ===
INFO:pisa.utils:Function: _fetch_isopolygons
INFO:pisa.utils:Cache file: mapbox_cache/f6ec0774b653ea5b75430c3c922786eb9f4d9dec36261770cd0abd1347b484d3.pkl
INFO:pisa.utils:Cache HIT - Loading cached result


INFO:pisa.utils:
=== Cache Status ===
INFO:pisa.utils:Function: _fetch_isopolygons
INFO:pisa.utils:Cache file: mapbox_cache/051c1d21d8f055260fa4e5eea74a359716d88d51e2e67b8856ec1562cd250def.pkl
INFO:pisa.utils:Cache HIT - Loading cached result
INFO:pisa.utils:
=== Cache Status ===
INFO:pisa.utils:Function: _fetch_isopolygons
INFO:pisa.utils:Cache file: mapbox_cache/fa43b2506fb7d88d9fb52408b59a1ae75794eab9520ceb752e253bdd84f50784.pkl
INFO:pisa.utils:Cache HIT - Loading cached result
INFO:pisa.utils:
=== Cache Status ===
INFO:pisa.utils:Function: _fetch_isopolygons
INFO:pisa.utils:Cache file: mapbox_cache/e8bbd73f086ebefdfa9c8bcafeaa362f1b9df916efbaa7c1c1072223db26d280.pkl
INFO:pisa.utils:Cache HIT - Loading cached result
INFO:pisa.utils:
=== Cache Status ===
INFO:pisa.utils:Function: _fetch_isopolygons
INFO:pisa.utils:Cache file: mapbox_cache/64efa06a4fde446a72a763390900aa76ad22a5106e47eb122c603c96dc51c8a5.pkl
INFO:pisa.utils:Cache HIT - Loading cached result
INFO:pisa.utils:
=== Cache S

### Prepare optimization data



In [67]:
population_served_current = get_population_served_by_isopolygons(
    grouped_population=population_gdf, isopolygons=isopolygons_existing_facilities
)

current = {DISTANCE_TYPE: population_served_current}

In [68]:
population_served_potential = get_population_served_by_isopolygons(
    grouped_population=population_gdf, isopolygons=isopolygons_potential_facilities
)

potential = {DISTANCE_TYPE: population_served_potential}

In [69]:
population_count = population_gdf.population.values

In [70]:
BUDGET = [
    5,
    20,
    50,
]  # budget for the optimization in terms of how many locations can be built

cbc_optimize = partial(jg_opt.OpenOptimize, solver_path=CBC_SOLVER_PATH)

values, solutions = jg_opt.Solve(
    household=population_count,
    current=current,
    potential=potential,
    accessibility=DISTANCE_TYPE,
    budgets=BUDGET,
    optimize=cbc_optimize,
    type="ID",
)

In [71]:
values

10000      5000      2000
5   0.474926  0.285802  0.142557
20  0.493441  0.309370  0.149697
50  0.497871  0.318868  0.153562

In [72]:
solutions

10000  \
5                                [27, 22, 39, 41, 18]   
20  [27, 22, 39, 41, 18, 10, 25, 20, 29, 51, 16, 8...   
50  [27, 22, 39, 41, 18, 10, 25, 20, 29, 51, 16, 8...   

                                                 5000  \
5                                [25, 22, 27, 28, 43]   
20  [25, 22, 27, 28, 43, 39, 16, 26, 8, 41, 36, 23...   
50  [25, 22, 27, 28, 43, 39, 16, 26, 8, 41, 36, 23...   

                                                 2000  
5                                 [39, 20, 27, 7, 43]  
20  [39, 20, 27, 7, 43, 25, 10, 13, 6, 22, 42, 26,...  
50  [39, 20, 27, 7, 43, 25, 10, 13, 6, 22, 42, 26,...